## ETL - EDA

In [170]:
import pandas as pd
import numpy as np

from ydata_profiling import ProfileReport

Primero, voy a leer el dataset

In [133]:
df=pd.read_csv('Datasets/AccidentesAviones.csv',index_col=0)

In [134]:
df.head()

fecha HORA declarada                                Ruta  \
0  September 17, 1908           1718                 Fort Myer, Virginia   
1  September 07, 1909              ?             Juvisy-sur-Orge, France   
2       July 12, 1912           0630           Atlantic City, New Jersey   
3     August 06, 1913              ?  Victoria, British Columbia, Canada   
4  September 09, 1913           1830                  Over the North Sea   

                 OperadOR flight_no          route                 ac_type  \
0    Military - U.S. Army         ?  Demonstration        Wright Flyer III   
1                       ?         ?       Air show          Wright Byplane   
2    Military - U.S. Navy         ?    Test flight               Dirigible   
3                 Private         ?              ?        Curtiss seaplane   
4  Military - German Navy         ?              ?  Zeppelin L-1 (airship)   

  registration cn_ln all_aboard PASAJEROS A BORDO crew_aboard  \
0            ?     1          2                 1           1   
1          SC1     ?          1                 0           1   
2            ?     ?          5                 0           5   
3            ?     ?          1                 0           1   
4            ?     ?         20                 ?           ?   

  cantidad de fallecidos passenger_fatalities crew_fatalities ground  \
0                      1                    1               0      0   
1                      1                    0               0      0   
2                      5                    0               5      0   
3                      1                    0               1      0   
4                     14                    ?               ?      0   

                                             summary  
0  During a demonstration flight, a U.S. Army fly...  
1  Eugene Lefebvre was the first pilot to ever be...  
2  First U.S. dirigible Akron exploded just offsh...  
3  The first fatal airplane accident in Canada oc...  
4  The airship flew into a thunderstorm and encou...

Muchas columnas del dataset tienen valores '?', los cuales asumiré que corresponden a valores nulos porque, como vemos a continuación, realmente no hay valores que pandas haya interpretado como NaN. 

In [135]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5008 entries, 0 to 5007
Data columns (total 17 columns):
 #   Column                  Non-Null Count  Dtype 
---  ------                  --------------  ----- 
 0   fecha                   5008 non-null   object
 1   HORA declarada          5008 non-null   object
 2   Ruta                    5008 non-null   object
 3   OperadOR                5008 non-null   object
 4   flight_no               5008 non-null   object
 5   route                   5008 non-null   object
 6   ac_type                 5008 non-null   object
 7   registration            5008 non-null   object
 8   cn_ln                   5008 non-null   object
 9   all_aboard              5008 non-null   object
 10  PASAJEROS A BORDO       5008 non-null   object
 11  crew_aboard             5008 non-null   object
 12  cantidad de fallecidos  5008 non-null   object
 13  passenger_fatalities    5008 non-null   object
 14  crew_fatalities         5008 non-null   object
 15  grou

Ahora, lo primero que haré es reemplazar todos los valores que aparecen como '?' por NaN y luego voy a eliminar las columnas que de entrada creo que no me van a servir para nada: el número del vuelo, registro, cn_ln (que parece ser algun número de serie) y summary, que es una descripción del evento.

In [136]:
df.replace('?',np.nan,inplace=True)

In [137]:
df.drop(columns=['flight_no','registration','cn_ln','summary'],inplace=True)

Ahora, voy a revisar nuevamente la cantidad de valores nulos

In [138]:
df.isna().sum()

fecha                        0
HORA declarada            1504
Ruta                         5
OperadOR                    10
route                      762
ac_type                     13
all_aboard                  17
PASAJEROS A BORDO          221
crew_aboard                219
cantidad de fallecidos       8
passenger_fatalities       235
crew_fatalities            235
ground                      44
dtype: int64

Voy a eliminar los datos nulos de cantidad de fallecidos, ya que me interesa hacer un análisis de la tasa de mortalidad y si hay registros que no tienen ese dato, no me van a ser de mucha utilidad.

In [139]:
df.dropna(subset='cantidad de fallecidos',inplace=True)

Ahora, veo que las columnas estan horriblemente escritas, voy a poner todos esos nombres en minúsculas.

In [140]:
df.columns= df.columns.str.lower()

Tengo un campo de fecha que realmente no me sirve en el análisis porque es un string, así que voy a cambiarle el formato y dejarlo en formato YYYY-MM-DD. Primero, voy a separar los datos por los espacios y los voy a asignar a nuevas columnas en el dataframe.

In [141]:
df[['mes','dia','anio']]=df['fecha'].str.split(' ', expand=True)

Ahora, ya que tengo esto, tengo que cambiar el formato de los días que quedaron con una coma al final. Para estoy voy a reemplazar la coma con un valor vacío.

In [142]:
df['dia']=df.dia.str.replace(',','')

Ahora, en la columna mes voy a reemplazar el mes por el número representativo de cada mes. 

In [143]:
df['mes']=pd.to_datetime(df['mes'], format='%B').dt.month

Ahora asignaré a la columna fecha la combinación de las columnas anio, mes y día y quitaré estas columnas, dejando solo la columna de fecha.

In [144]:
df['fecha']=df['anio'].astype(str)+'-'+df['mes'].astype(str)+'-'+df['dia'].astype(str)

In [145]:
df.drop(columns=['mes','dia','anio'],inplace=True)

In [146]:
df

fecha hora declarada                                ruta  \
0     1908-9-17           1718                 Fort Myer, Virginia   
1     1909-9-07            NaN             Juvisy-sur-Orge, France   
2     1912-7-12           0630           Atlantic City, New Jersey   
3     1913-8-06            NaN  Victoria, British Columbia, Canada   
4     1913-9-09           1830                  Over the North Sea   
...         ...            ...                                 ...   
5003  2021-3-28           1835                  Near Butte, Alaska   
5004  2021-5-21           1800                Near Kaduna, Nigeria   
5005  2021-6-10           0800          Near Pyin Oo Lwin, Myanmar   
5006  2021-7-04          11:30          Patikul, Sulu, Philippines   
5007  2021-7-06           1500                      Palana, Russia   

                             operador                         route  \
0                Military - U.S. Army                 Demonstration   
1                                 NaN                      Air show   
2                Military - U.S. Navy                   Test flight   
3                             Private                           NaN   
4              Military - German Navy                           NaN   
...                               ...                           ...   
5003                Soloy Helicopters           Sightseeing Charter   
5004    Military - Nigerian Air Force                           NaN   
5005     Military - Myanmar Air Force          Naypyidaw - Anisakan   
5006  Military - Philippine Air Force  Cagayan de Oro-Lumbia - Jolo   
5007    Kamchatka Aviation Enterprise        Petropavlovsk - Palana   

                            ac_type all_aboard pasajeros a bordo crew_aboard  \
0                  Wright Flyer III          2                 1           1   
1                    Wright Byplane          1                 0           1   
2                         Dirigible          5                 0           5   
3                  Curtiss seaplane          1                 0           1   
4            Zeppelin L-1 (airship)         20               NaN         NaN   
...                             ...        ...               ...         ...   
5003    Eurocopter AS350B3 Ecureuil          6                 5           1   
5004  Beechcraft B300 King Air 350i         11                 7           4   
5005               Beechcraft 1900D         14                12           2   
5006       Lockheed C-130H Hercules         96                88           8   
5007             Antonov An 26B-100         28                22           6   

     cantidad de fallecidos passenger_fatalities crew_fatalities ground  
0                         1                    1               0      0  
1                         1                    0               0      0  
2                         5                    0               5      0  
3                         1                    0               1      0  
4                        14                  NaN             NaN      0  
...                     ...                  ...             ...    ...  
5003                      5                    4               1      0  
5004                     11                    7               4      0  
5005                     12                   11               1      0  
5006                     50                  NaN             NaN      3  
5007                     28                   22               6      0  

[5000 rows x 13 columns]

In [147]:
df.isna().sum()

fecha                        0
hora declarada            1496
ruta                         5
operador                    10
route                      755
ac_type                     11
all_aboard                   9
pasajeros a bordo          213
crew_aboard                211
cantidad de fallecidos       0
passenger_fatalities       227
crew_fatalities            227
ground                      36
dtype: int64

Ahora, para mi análisis quisiera revisar solo los vuelos que tuvieron fatalidades, así que voy a eliminar los registros que no tienen fatalidades. 

In [148]:
df[df['cantidad de fallecidos']=='0']

fecha hora declarada                                 ruta  \
30    1919-10-20            NaN  English Channel off Forkstone, Kent   
117   1926-10-21        c 13:15                      English Channel   
120    1927-1-12            NaN                     Estaires, France   
289    1932-8-12            NaN                    Beyrouth, Lebanon   
323   1933-11-10            NaN                 Moriarty, New Mexico   
...          ...            ...                                  ...   
4708  2008-12-20           1818                     Denver, Colorado   
4712   2009-1-15           1506                   New York, New York   
4839   2012-6-02           1530                         Accra, Ghana   
4863   2013-4-13           1535                  Denpasar, Indonesia   
4937   2016-8-05           1238          Dubai, United Arab Emirates   

                               operador  \
30        Aircraft Transport and Travel   
117                    Imperial Airways   
120                              Fokker   
289                          Air Orient   
323   Trans Continental and Western Air   
...                                 ...   
4708               Continental Airlines   
4712                         US Airways   
4839                         Allied Air   
4863                           Lion Air   
4937                           Emirates   

                                       route            ac_type all_aboard  \
30                                       NaN  De Havilland DH-4          0   
117                          Croydon - Paris  Handley Page W-10         12   
120                          Delivery flight       Fokker F-VII          0   
289   Marseille - Naples - Beyrouth - Saigon            CAMS 53          7   
323                                      NaN     Northrop Delta          1   
...                                      ...                ...        ...   
4708                        Denver - Houston     Boeing 737-500        115   
4712             New York, NY- Charlotte, NC    Airbus A320-214        155   
4839           Lagos, Nigerai - Accra, Ghana   Boeing B-727-200          4   
4863                      Bandung - Denpasar   Boeing B-737-8GP        108   
4937    Thiruvanthapuram, India - Dubai, UAE     Boeing 777-31H        300   

     pasajeros a bordo crew_aboard cantidad de fallecidos  \
30                   0           1                      0   
117                 10           2                      0   
120                  0           2                      0   
289                  3           4                      0   
323                  0           1                      0   
...                ...         ...                    ...   
4708               110           5                      0   
4712               150           5                      0   
4839                 0           4                      0   
4863               101           7                      0   
4937               282          18                      0   

     passenger_fatalities crew_fatalities ground  
30                      0               0      0  
117                     0               0      0  
120                     0               2      0  
289                     0               0      0  
323                     0               0      0  
...                   ...             ...    ...  
4708                    0               0      0  
4712                    0               0      0  
4839                    0               4     12  
4863                    0               0      0  
4937                    0               0      1  

[76 rows x 13 columns]

In [149]:
df=df[df['cantidad de fallecidos']!='0']

Ahora, me di cuenta mirando los vuelos que no tuvieron fatalidades que la columna route parece no tener informacion consistente, unos valores parecen ser el tipo de vuelo que se estaba haciendo y otros el destino al que queria llegar el vuelo, quiero revisar esto mas a fondo. 

In [150]:
df['route']

0                      Demonstration
1                           Air show
2                        Test flight
3                                NaN
4                                NaN
                    ...             
5003             Sightseeing Charter
5004                             NaN
5005            Naypyidaw - Anisakan
5006    Cagayan de Oro-Lumbia - Jolo
5007          Petropavlovsk - Palana
Name: route, Length: 4924, dtype: object

Lo ultimo que veo, son nombres de ciudades y al comienzo el tipo de vuelo, voy a eliminar esta columna porque me parece inconsistente.

In [151]:
df.drop(columns='route',inplace=True)

C:\Users\ksfaj\AppData\Local\Temp\ipykernel_11648\3359113153.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.drop(columns='route',inplace=True)


In [152]:
df.head()

fecha hora declarada                                ruta  \
0  1908-9-17           1718                 Fort Myer, Virginia   
1  1909-9-07            NaN             Juvisy-sur-Orge, France   
2  1912-7-12           0630           Atlantic City, New Jersey   
3  1913-8-06            NaN  Victoria, British Columbia, Canada   
4  1913-9-09           1830                  Over the North Sea   

                 operador                 ac_type all_aboard  \
0    Military - U.S. Army        Wright Flyer III          2   
1                     NaN          Wright Byplane          1   
2    Military - U.S. Navy               Dirigible          5   
3                 Private        Curtiss seaplane          1   
4  Military - German Navy  Zeppelin L-1 (airship)         20   

  pasajeros a bordo crew_aboard cantidad de fallecidos passenger_fatalities  \
0                 1           1                      1                    1   
1                 0           1                      1                    0   
2                 0           5                      5                    0   
3                 0           1                      1                    0   
4               NaN         NaN                     14                  NaN   

  crew_fatalities ground  
0               0      0  
1               0      0  
2               5      0  
3               1      0  
4             NaN      0

Veo que la columna hora declarada tampoco tiene un formato uniforme, voy a normalizarla poniendo todos los valores como 4 numeros consecutivos. Como se que los datos estan en formato string, voy a filtrar los datos por los que tienen mas de 4 caracteres y usar replace para reemplazar por vacios los caracteres que no quiero.

In [153]:
df[df['hora declarada'].str.len()>4]

fecha hora declarada                                     ruta  \
84     1923-9-14        c 18:00  Near Ivinghoe, Buckinghamshire, England   
87    1923-12-23        c 02:30               Over the Mediterranean Sea   
95    1924-12-24        c 12:00                          Purley, England   
132    1927-9-23          10:00                         Schleiz, Germany   
156    1928-7-24          14:48                   Waalhaven, Netherlands   
...          ...            ...                                      ...   
4380   2002-2-22          02:30               Off Dumaguete, Philippines   
4385   2002-4-15          11:23                       Busan, South Korea   
4531  2004-12-11          05:30                          Uberaba, Brazil   
4742   2009-8-26          0500Z                    Nganga Lingolo, Congo   
5006   2021-7-04          11:30               Patikul, Sulu, Philippines   

                             operador                      ac_type all_aboard  \
84                    Daimler Airways           de Havilland DH-34          5   
87             Military - French Navy  Zeppelin Dixmunde (airship)         52   
95                   Imperial Airways          de Havilland DH-34B          8   
132                Deutsche Lufthansa               Dornier Merkur          6   
156          KLM Royal Dutch Airlines           Fokker (KLM) F.III          6   
...                               ...                          ...        ...   
4380             Military - U.S. Army     MH-47 Chinook helicopter         10   
4385                        Air China           Boeing B-767-200ER        166   
4531                   NHR Táxi-Aéreo  Embraer EMB-110 Bandeirante          2   
4742               Aero Fret Business              Antonov An-12BK          7   
5006  Military - Philippine Air Force     Lockheed C-130H Hercules         96   

     pasajeros a bordo crew_aboard cantidad de fallecidos  \
84                   3           2                      5   
87                 NaN         NaN                     52   
95                   7           1                      8   
132                  4           2                      6   
156                  5           1                      1   
...                ...         ...                    ...   
4380                 4           6                     10   
4385               155          11                    128   
4531                 0           2                      2   
4742                 2           5                      7   
5006                88           8                     50   

     passenger_fatalities crew_fatalities ground  
84                      3               2      0  
87                    NaN             NaN      0  
95                      7               1      0  
132                     4               2      0  
156                     1               0      0  
...                   ...             ...    ...  
4380                    4               6      0  
4385                  120               8      0  
4531                    0               2      1  
4742                    2               5      0  
5006                  NaN             NaN      3  

[208 rows x 12 columns]

In [154]:
df['hora declarada']=df['hora declarada'].str.replace(':','')

C:\Users\ksfaj\AppData\Local\Temp\ipykernel_11648\188119120.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['hora declarada']=df['hora declarada'].str.replace(':','')


In [155]:
df['hora declarada']=df['hora declarada'].str.replace('c','')

C:\Users\ksfaj\AppData\Local\Temp\ipykernel_11648\1917597562.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['hora declarada']=df['hora declarada'].str.replace('c','')


Estos datos a los que le quite la c tienen un espacio antes de la hora, se lo quitare con la funcion strip.

In [156]:
df['hora declarada']=df['hora declarada'].str.strip()

C:\Users\ksfaj\AppData\Local\Temp\ipykernel_11648\3999901665.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['hora declarada']=df['hora declarada'].str.strip()


Reviso nuevamente que datos me quedan por normalizar.

In [157]:
df[df['hora declarada'].str.len()>4]

fecha hora declarada                   ruta  \
881    1946-8-20          06;15          Rouen, France   
926   1946-12-28          0209Z  Near Shannon, Ireland   
1120   1949-7-12          0350Z     Near Bombay, India   
1308   1952-2-16          1734Z     Near Burgio, Italy   
1340   1952-8-21          0100Z     Off Trapani, Italy   
4742   2009-8-26          0500Z  Nganga Lingolo, Congo   

                               operador                             ac_type  \
881            British Overseas Airways              Avro 691 Lancastrian 1   
926   Trans Continental and Western Air           Lockheed 049 Consellation   
1120           KLM Royal Dutch Airlines  Lockheed L-749-79-33 Constellation   
1308                 Hunting Air Travel                Vickers 614 Viking 1   
1340                            Airwork        Handley Page HP-81 Hermes 4A   
4742                 Aero Fret Business                     Antonov An-12BK   

     all_aboard pasajeros a bordo crew_aboard cantidad de fallecidos  \
881           9                 0           9                      8   
926          23                14           9                     13   
1120         45                34          11                     45   
1308         31                26           5                     31   
1340         57                51           6                      7   
4742          7                 2           5                      7   

     passenger_fatalities crew_fatalities ground  
881                     0               8      0  
926                     9               4      0  
1120                   34              11      0  
1308                   26               5      0  
1340                    1               6      0  
4742                    2               5      0

In [158]:
df['hora declarada']=df['hora declarada'].str.replace('Z','')

C:\Users\ksfaj\AppData\Local\Temp\ipykernel_11648\46654327.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['hora declarada']=df['hora declarada'].str.replace('Z','')


In [159]:
df['hora declarada']=df['hora declarada'].str.replace(';','')

C:\Users\ksfaj\AppData\Local\Temp\ipykernel_11648\3361306016.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['hora declarada']=df['hora declarada'].str.replace(';','')


Compruebo que no queden datos por normalizar y cuento nuevamente cuantos valores nulos hay para tener en cuenta cuando convierta a formato hora que no me aparezcan mas valores nulos.

In [160]:
df[df['hora declarada'].str.len()>4]

Empty DataFrame
Columns: [fecha, hora declarada, ruta, operador, ac_type, all_aboard, pasajeros a bordo, crew_aboard, cantidad de fallecidos, passenger_fatalities, crew_fatalities, ground]
Index: []

In [161]:
df['hora declarada'].isna().sum()

1479

Ahora, para comparar valores, voy a poner en una nueva columna la hora con el formato de tiempo por si me aparecen mas valores NaN cuando convierta.

In [162]:
df['hora']=pd.to_datetime(df['hora declarada'], format='%H%M').dt.time

C:\Users\ksfaj\AppData\Local\Temp\ipykernel_11648\992038580.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['hora']=pd.to_datetime(df['hora declarada'], format='%H%M').dt.time


In [163]:
df.hora.isna().sum()

1479

Me dio el mismo numero asi que la transformacion fue satisfactoria, voy a eliminar la columna hora declarada.

In [164]:
df.drop(columns=['hora declarada'],inplace=True)

C:\Users\ksfaj\AppData\Local\Temp\ipykernel_11648\2513194787.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.drop(columns=['hora declarada'],inplace=True)


In [165]:
df

fecha                                ruta  \
0     1908-9-17                 Fort Myer, Virginia   
1     1909-9-07             Juvisy-sur-Orge, France   
2     1912-7-12           Atlantic City, New Jersey   
3     1913-8-06  Victoria, British Columbia, Canada   
4     1913-9-09                  Over the North Sea   
...         ...                                 ...   
5003  2021-3-28                  Near Butte, Alaska   
5004  2021-5-21                Near Kaduna, Nigeria   
5005  2021-6-10          Near Pyin Oo Lwin, Myanmar   
5006  2021-7-04          Patikul, Sulu, Philippines   
5007  2021-7-06                      Palana, Russia   

                             operador                        ac_type  \
0                Military - U.S. Army               Wright Flyer III   
1                                 NaN                 Wright Byplane   
2                Military - U.S. Navy                      Dirigible   
3                             Private               Curtiss seaplane   
4              Military - German Navy         Zeppelin L-1 (airship)   
...                               ...                            ...   
5003                Soloy Helicopters    Eurocopter AS350B3 Ecureuil   
5004    Military - Nigerian Air Force  Beechcraft B300 King Air 350i   
5005     Military - Myanmar Air Force               Beechcraft 1900D   
5006  Military - Philippine Air Force       Lockheed C-130H Hercules   
5007    Kamchatka Aviation Enterprise             Antonov An 26B-100   

     all_aboard pasajeros a bordo crew_aboard cantidad de fallecidos  \
0             2                 1           1                      1   
1             1                 0           1                      1   
2             5                 0           5                      5   
3             1                 0           1                      1   
4            20               NaN         NaN                     14   
...         ...               ...         ...                    ...   
5003          6                 5           1                      5   
5004         11                 7           4                     11   
5005         14                12           2                     12   
5006         96                88           8                     50   
5007         28                22           6                     28   

     passenger_fatalities crew_fatalities ground      hora  
0                       1               0      0  17:18:00  
1                       0               0      0       NaT  
2                       0               5      0  06:30:00  
3                       0               1      0       NaT  
4                     NaN             NaN      0  18:30:00  
...                   ...             ...    ...       ...  
5003                    4               1      0  18:35:00  
5004                    7               4      0  18:00:00  
5005                   11               1      0  08:00:00  
5006                  NaN             NaN      3  11:30:00  
5007                   22               6      0  15:00:00  

[4924 rows x 12 columns]

In [166]:
df.isna().sum()

fecha                        0
ruta                         5
operador                    10
ac_type                     11
all_aboard                   9
pasajeros a bordo          212
crew_aboard                210
cantidad de fallecidos       0
passenger_fatalities       225
crew_fatalities            225
ground                      36
hora                      1479
dtype: int64

Ahora, tampoco puedo calcular la tasa de mortalidad si no se cuantas personas iban a bordo en total, voy a revisar los registros de esta columna que aparecen como NaN.

In [167]:
df[df.all_aboard.isna()]

fecha                                     ruta  \
26     1919-7-21                        Chicago, Illinois   
1231   1951-1-20                             Huilyo, Peru   
1362  1952-12-22                          Damascus, Syria   
1386   1953-4-10             Near Anchieta Island, Brazil   
1577   1956-6-13                      Over North Carolina   
1627   1957-4-20                            Jirkouk, Iraq   
1638   1957-6-24       Horn Island, Queensland, Australia   
3553   1989-5-09                      Near Tainjin, China   
3752   1992-2-20  En route from Argentina  to  California   

                                operador                       ac_type  \
26    Wingfoot Air Express Goodyear Tire             FD Type Dirigible   
1231                      Military - TAM                  Douglas DC-3   
1362                          Syrian Air                  Douglas DC-3   
1386                                REAL                  Doublas Dc-3   
1577                            Piedmont                  Douglas DC-3   
1627                          Air France  Lockheed Super Constellation   
1638                     Adastra Airways                      L-Hudson   
3553                          Aero Asahi                      Bell 412   
3752               Aerolineas Argentinas                  Boeing B-747   

     all_aboard pasajeros a bordo crew_aboard cantidad de fallecidos  \
26          NaN               NaN         NaN                      3   
1231        NaN               NaN         NaN                     16   
1362        NaN               NaN         NaN                      9   
1386        NaN               NaN         NaN                     26   
1577        NaN               NaN         NaN                      1   
1627        NaN               NaN         NaN                      1   
1638        NaN               NaN         NaN                      6   
3553        NaN               NaN         NaN                     10   
3752        NaN               NaN         NaN                      1   

     passenger_fatalities crew_fatalities ground      hora  
26                      2               1     10  16:55:00  
1231                  NaN             NaN    NaN       NaT  
1362                  NaN             NaN    NaN       NaT  
1386                  NaN             NaN    NaN       NaT  
1577                    1             NaN      0       NaT  
1627                    1               0      0       NaT  
1638                  NaN             NaN    NaN       NaT  
3553                  NaN             NaN      0       NaT  
3752                  NaN             NaN      0       NaT

Realmente no tengo manera de saber cuantas personas en total iban a bordo asi que voy a eliminar estos registros. 

In [168]:
df.dropna(subset='all_aboard',inplace=True)

C:\Users\ksfaj\AppData\Local\Temp\ipykernel_11648\1016923586.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.dropna(subset='all_aboard',inplace=True)


In [171]:
ProfileReport(df)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]